In [108]:
import logging

logging.basicConfig(format="%(levelname)s - %(name)s -  %(message)s", level=logging.WARNING)
logging.getLogger("haystack").setLevel(logging.INFO)


In [110]:
import os
from haystack.document_stores import InMemoryDocumentStore
document_store = InMemoryDocumentStore(use_bm25=True)

doc_dir = './documents'


INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1


In [111]:
from haystack import Pipeline
from haystack.nodes import TextConverter, PreProcessor

indexing_pipeline = Pipeline()
text_converter = TextConverter()
preprocessor = PreProcessor(
    clean_whitespace=True,
    clean_header_footer=True,
    clean_empty_lines=True,
    split_by="word",
    split_length=1000,
    split_overlap=20,
    split_respect_sentence_boundary=True,
)



In [112]:
import os

indexing_pipeline.add_node(component=text_converter, name="TextConverter", inputs=["File"])
indexing_pipeline.add_node(component=preprocessor, name="PreProcessor", inputs=["TextConverter"])
indexing_pipeline.add_node(component=document_store, name="DocumentStore", inputs=["PreProcessor"])


In [113]:
files_to_index = [doc_dir + "/" + f for f in os.listdir(doc_dir)]
indexing_pipeline.run_batch(file_paths=files_to_index)


INFO - haystack.pipelines.base -  It seems that an indexing Pipeline is run, so using the nodes' run method instead of run_batch.
Updating BM25 representation...: 100%|██████████| 2880/2880 [00:01<00:00, 2667.45 docs/s]


{'documents': [<Document: {'content': '==============================================================\nGuild: BDynamics (VTOL VR)\nChannel: Collaborate / map_editor\nTopic: Discuss the map editor, share custom maps, post map related screenshots, etc.\n==============================================================\n\n[02/18/2019 4:40 PM] Spessforce1701#6135\nhey wait a second\n\n[02/18/2019 4:40 PM] Spessforce1701#6135\nhow long has this been here\n\n[02/18/2019 4:41 PM] Scruffy#9436\n**?** Huh? Whose footprints are these?\n\n[02/18/2019 4:42 PM] hizokuto#9224\nLMFAO\n\n[02/18/2019 4:42 PM] hizokuto#9224\nWHAT THE SHIT\n\n[02/18/2019 4:42 PM] Ketkev#0002\nooooh spicy\n\n[02/18/2019 4:43 PM] Scruffy#9436\nThis is pretty cool. Would love to see what kind of maps people make\n\n[02/18/2019 4:43 PM] Scruffy#9436\n*Because I am garbo at making them*\n\n[02/18/2019 4:43 PM] hizokuto#9224\n@Calius there\'s a place for just your maps\n\n[02/18/2019 4:43 PM] Ketkev#0002\ni dont create good maps\

In [115]:
from haystack.nodes import BM25Retriever

retriever = BM25Retriever(document_store=document_store)


In [116]:
from haystack.nodes import Seq2SeqGenerator

generator = Seq2SeqGenerator(model_name_or_path="vblagoje/bart_lfqa")

INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
/home/friendlybandit/haystack_search/venv/lib/python3.8/site-packages/torch/_utils.py:776: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


In [117]:
from haystack.pipelines import GenerativeQAPipeline

pipeline = GenerativeQAPipeline(generator=generator, retriever=retriever)

In [118]:
question = "How do I chaff a missile in VTOL VR?"

prediction = pipeline.run(
    query=question,
    params={
        "Retriever": {"top_k": 10},
    }
)


In [119]:
from haystack.utils import print_answers

print_answers(
    prediction,
    details="medium" ## Choose from `minimum`, `medium` and `all`
)


'Query: How do I chaff a missile in VTOL VR?'
'Answers:'
[   {   'answer': 'There are two ways to chaff a missile in VTOL VR. The first '
                  'is to hold down the drop munitions button and then press it '
                  'multiple times. The second way is to go into the equip/SMS '
                  'page and then put the GPS target mode (might not be called '
                  'this exactly but you will notice it) to auto drop '
                  'munitions.'}]
